## Question 4

For Q4-Q6 we'll reproduce what we did in the module, but with a different GitHub repo.

We'll use the podcasts archive from DataTalks.Club: https://datatalks.club/podcast.html

The data is available here: https://github.com/DataTalksClub/datatalksclub.github.io/tree/main/_podcast

Download the data (only for podcasts). How many records are there?

In [1]:
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.common.by import By
import requests
from urllib.parse import urljoin


url = 'https://github.com/DataTalksClub/datatalksclub.github.io/tree/main/_podcast'


options = webdriver.ChromeOptions()
options.add_argument("--headless=new")
driver = webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)

driver.get(url)

a_elements = driver.find_elements(By.TAG_NAME, 'a')

filenames=[]
seen=set()
for a in a_elements:
    title = a.get_attribute('title')
    # if href and href.endswith(('.md')):
    if title.endswith(('.md')):
        if title in seen:
            continue
        seen.add(title)
        filenames.append(title)

In [2]:
print(f'There are {len(filenames)} records.')

There are 185 records.


# Question 5

Let's prepare this data. It's already structured, so you can chunk it using paragraphs. Let's do chunk size 30 and overlap 15. How many chunks do you have in the result?

In [ ]:
import requests
import frontmatter
from tqdm.auto import tqdm
import re

podcasts = []
for f in tqdm(filenames):
    url = f'https://raw.githubusercontent.com/DataTalksClub/datatalksclub.github.io/refs/heads/main/_podcast/{f}'

    r = requests.get(url, timeout=30)
    raw = r.text
    content = re.sub(r'\{\{.*?\}\}', 'TEMPLATE_VAR', raw)
    post = frontmatter.loads(content)
    data = post.to_dict()
    data['filename'] = f
    podcasts.append(data)
podcasts
# flattened = []
# for p in podcasts:
#     attrs = p.get('attributes', {})
#     record = {**attrs}
#     record['transcript'] = p.get('transcript', '')
#     record['filename'] = p.get('filename', '')
#     flattened.append(record)

In [ ]:
# podcasts_all = []

# p = podcasts[0]
# transcript = p.get('transcript')
# filename = p.get('filename')


# for t in transcript:
#     line = t.get('line')

#     podcasts_all.append(
#         {'paragraph': line,
#          'filename': filename}
#     )

# podcasts_all



podcasts_all = []
for p in podcasts:
    transcript = p.get('transcript', {})
    for t in transcript:
        if t.get('line') is None:
            continue
        line = t.get('line')
        podcasts_all.append(
            {'paragraph': line,
            'title': p.get('title'),
            'filename': p.get('filename')}
        )
podcasts_all
    

In [ ]:
# flattened = []

# for p in podcasts:
#     transcript = p.get("transcript", {})
#     # print(transcript)
#     chunks = transcript.get("chunk", []) if isinstance(transcript, dict) else transcript
#     print(chunks)
#     print(p.get('title'))
    # lines = [c["line"] for c in chunks if isinstance(c, dict) and "line" in c]
    # print(lines)
    # merged_text = " ".join(lines).strip()

    # flattened.append({
    #     "title": p.get("title"),
    #     "episode": p.get("episode"),
    #     "text": merged_text
    # })
# flattened

In [6]:
def chunk_by_paragraphs(paragraphs, size=30, step=15):
    if size <= 0 or step <= 0:
        raise ValueError("size and step must be positive")
    n = len(paragraphs)

    chunks = []
    for i in range(0, n, size):
        chunk = paragraphs[i:i + step]
        if not chunk:
            break
        chunks.append({'start': i, 'chunk': chunk})
        if i + size >= n:
            break
    return chunks

In [7]:
from itertools import groupby
from operator import itemgetter

# for p in podcasts:
podcasts_sorted = sorted(podcasts_all, key=itemgetter('title'))

all_chunks=[]
for title, paragraph in groupby(podcasts_sorted, key=itemgetter('title')):
    paragraph_list = list(paragraph)
    chunks = chunk_by_paragraphs(paragraph_list)
    for c in chunks:
        all_chunks.append({'title': title, 'paragraphs':c})
all_chunks

[{'title': 'A/B Testing',
  'paragraphs': {'start': 0,
   'chunk': [{'paragraph': "This week we'll talk about A/B testing and experimentation. We have a special guest today, Jakob. Jakob has more than three years of experience of growing data analytics teams. Now he's a head of analytics at Inkitt. He's passionate about A/B tests, defining metrics, and pizza dough. Welcome, Jakob.",
     'title': 'A/B Testing',
     'filename': 's07e06-ab-testing.md'},
    {'paragraph': 'Yeah, thanks for having me.',
     'title': 'A/B Testing',
     'filename': 's07e06-ab-testing.md'},
    {'paragraph': "I’m especially curious about the last point – the pizza dough. But maybe this is something that we'll talk about later. But before we go into our main topic of A/B tests, let's start with your background. Can you tell us about your career journey so far?",
     'title': 'A/B Testing',
     'filename': 's07e06-ab-testing.md'},
    {'paragraph': "Sure, yeah. I guess my journey started with finishing my 

In [8]:
print(f'There are {len(all_chunks)} chunks.')

There are 879 chunks.


# Question 6

Index the data with Index from minsearch. What's the first episode in the results for "how do I make money with AI?"



In [ ]:
from minsearch import Index

index = Index(
    text_fields=['chunk', 'title', 'filename']
)

index.fit(all_chunks)


In [10]:
query = 'how do I make money with AI?'

print(f"'{index.search(query)[0]['title']}' is the first episode in the results.")

'Freelancing and Consulting with Data Engineering' is the first episode in the results.
